## Imports

In [1]:
# Make the good imports
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px

## Loading our DataFrame

In [2]:
#load the data
df = pd.read_csv('timeseries/blockchain_by_actor.csv', index_col=0, parse_dates=True)
df.tail()



year  month  day      identity  received  nb_received        date  \
90398   0.0    0.0  0.0    BTCJam.com       0.0          0.0  2017-06-17   
90399   0.0    0.0  0.0          7277       0.0          0.0  2017-06-18   
90400   0.0    0.0  0.0      70063369       0.0          0.0  2017-06-22   
90401   0.0    0.0  0.0  Loanbase.com       0.0          0.0  2017-06-29   
90402   0.0    0.0  0.0          7277       0.0          0.0  2017-06-29   

          sum_fee  mean_fee_for100  nb_transactions        sent  self_spent  \
90398    145053.0         8.643929              1.0   1387984.0         0.0   
90399  26600900.0        49.327293            266.0    725280.0         0.0   
90400    284134.0         0.301961              1.0  93527891.0         0.0   
90401    131862.0         1.415791              1.0   9049938.0         0.0   
90402  39601350.0        49.327299            396.0   1079730.0         0.0   

       self_spent_estimated  nb_spent       spent  
90398                   0.0       2.0   1387984.0  
90399                   0.0     532.0    725280.0  
90400                   0.0       1.0  93527891.0  
90401                   0.0       2.0   9049938.0  
90402                   0.0     792.0   1079730.0

We notice that there is a problem with the year, month, day columns and on several data types in the raw DataFrame.
Let's clean it in order to work in good conditions.

## Cleaning our data

In [3]:
df.dtypes

year                    float64
month                   float64
day                     float64
identity                 object
received                float64
nb_received             float64
date                     object
sum_fee                 float64
mean_fee_for100         float64
nb_transactions         float64
sent                    float64
self_spent              float64
self_spent_estimated    float64
nb_spent                float64
spent                   float64
dtype: object

In [4]:
# convert year, month and day to int
df['year'] = df['year'].astype(int)
df['month'] = df['month'].astype(int)
df['day'] = df['day'].astype(int)

# convert the date to datetime in year-month-day format
df['date'] = pd.to_datetime(df['date'], format='%Y-%m-%d')

# convert identity to string
df['identity'] = df['identity'].astype(str)

# convert nb_transactions, nb_received, nb_spent to int
df['nb_transactions'] = df['nb_transactions'].astype(int)
df['nb_received'] = df['nb_received'].astype(int)
df['nb_spent'] = df['nb_spent'].astype(int)


In [5]:
# get the year, month and day from the date
df['year'] = df['date'].dt.year
df['month'] = df['date'].dt.month
df['day'] = df['date'].dt.day

In [6]:
# save the df to a csv file
df.to_csv('timeseries/blockchain_by_actor_cleaned.csv')

# Analysis

In this notebook, we will analyze the **100 major actors** of the bitcoin blockchain between **2015 and 2017**. And we will try to identify the motivations of the actors and their behavior.

All results and calculations on amounts will be given in **Satoshi**.

In [7]:
# biggest spenders in df
biggest_spenders = df.groupby('identity')['spent'].sum().sort_values(ascending=False)

# plot the biggest spenders with plotly
# with x as the identity and y as the spent
# with a title and a label for the x and y axis
fig_spenders = px.bar(biggest_spenders, x=biggest_spenders.index, y=biggest_spenders.values, title='Biggest "spenders" in the bitcoin blockchain (2015-2017)', labels={'x':'Identity', 'y':'Spent'})
fig_spenders.show()

This plot, based on the spent column, represents the volume of satoshis sent to addresses other than those of the actors themselves.
We will focus on self-transactions later.

In [8]:
# biggest receivers
biggest_receivers = df.groupby('identity')['received'].sum().sort_values(ascending=False)

fig_receivers = px.bar(biggest_receivers, x=biggest_receivers.index, y=biggest_receivers.values, title='Biggest "receivers" in the bitcoin blockchain (2015-2017)', labels={'x':'Identity', 'y':'Received'})
fig_receivers.show()

In [9]:
# subplot of 2 pie with plotly with the biggest spenders and the biggest receivers

import plotly.graph_objects as go
from plotly.subplots import make_subplots

fig = make_subplots(rows=1, cols=2, specs=[[{'type':'domain'}, {'type':'domain'}]])
fig.add_trace(go.Pie(labels=biggest_spenders.index, values=biggest_spenders.values, name="Biggest spenders"), 1, 1)
fig.add_trace(go.Pie(labels=biggest_receivers.index, values=biggest_receivers.values, name="Biggest receivers"), 1, 2)
fig.update_traces(textposition='inside')
fig.update_layout(title_text="Biggest spenders and receivers in the bitcoin blockchain (% of the total spent and received)")
fig.show()


In [10]:
# get the names in a list of the 3 best identities in terms of spent column
best_spent = df.groupby('identity')['spent'].sum().sort_values(ascending=False).head(3).index.tolist()

fig_evolution = px.line(df[df['identity'].isin(best_spent)].groupby(['date', 'identity'])['spent'].sum().unstack().rolling(30).mean(), title='Evolution of the biggest spenders', labels={'value':'spent'}, height=600, width=1000)
fig_evolution.show()

# Study of transaction fees paid: Who pays the best on average?

Let's look at how the average transaction fee per transaction (mean_fee_for100) varies between players.

In [11]:
# full list: best fee/transaction over the (2015-2017) period
# best payer in terms of mean fee per transaction
# we can see a significant difference between the top 3 and the others

best_payers = df.groupby('identity')['mean_fee_for100'].mean().sort_values(ascending=False) 
best_payers

identity
7277             15.871148
999Dice.com       5.511470
419               5.106580
0                 4.907442
18972             4.186133
                   ...    
Paymium.com       0.011627
5162              0.009440
SlushPool.com     0.007377
69697250          0.005614
BTCC.com          0.002298
Name: mean_fee_for100, Length: 100, dtype: float64

In [12]:
# plot the best payers
fig_payers = px.bar(best_payers.head(100), title='Best payers in terms of mean fees per transaction', labels={'value':'mean fees/transaction(satoshi)'}, height=600, width=1000)
fig_payers.show()

## What is the relationship between the total transaction fees paid (sum_fee) and the number of transactions made (nb_transactions) for each actor?
Let's analyze the correlation between these two variables to see if actors who make more transactions also pay more fees.

In [13]:
# let's compute the correlation between the sum_fee and nb_transactions
df[['sum_fee', 'nb_transactions']].corr()

sum_fee  nb_transactions
sum_fee          1.000000         0.409517
nb_transactions  0.409517         1.000000

A correlation of 0.4 means that there is a moderate positive relationship between two variables. When the value of one variable increases/decreases, the value of the other variable tends to increase/decrease as well, but not systematically.

Therefore we can't say that the actors who carry out the greatest number of transactions will pay a greater amount of fees.

## Is there a relationship between the proportion of self-initiated transactions and the transaction fees paid by the actors?
Let's see if actors who self-initiate a higher proportion of transactions tend to pay different transaction fees than those who primarily send funds to third parties.

In [14]:
# compute the self spent proportion
df['self_spent_proportion'] = df['self_spent'] / df['sent'] * 100

# display the top 5 identities in terms of self spent proportion
df.groupby('identity')['self_spent_proportion'].mean().sort_values(ascending=False).head(5)


identity
Paymium.com               81.309526
ePay.info_CoinJoinMess    73.112700
Bitbond.com               68.926661
SimpleCoin.cz             68.501003
BitZillions.com           63.335812
Name: self_spent_proportion, dtype: float64

In [15]:
df_self_spent_prop_sorted = df.groupby('identity')['self_spent_proportion'].mean().sort_values(ascending=False)

In [16]:
fig = px.bar(df_self_spent_prop_sorted.head(100), title='Ranking the identities in terms of self spent proportion', labels={'index': 'identity', 'value': 'self spent proportion (in %)'}, height=600)
fig.show()


We can observe the nature of the actors in terms of spending. As we can see here, for some actors the proportion of self_spending is very high.

* **Paymium.com** for example is a french bitcoin exchange company that was founded in 2011, it is therefore not surprising that the majority of its transactions are self-initiated.





It is difficult to predict what are the intentions of such actors. Some might manage exchange platforms, that opper intern transactions for several reasons.

Others might use mixing techniques to hide their transactions, or to dissimulate the origin of their funds.

In [17]:
df_mean_fee_per_transaction = df.groupby('identity')['mean_fee_for100'].mean()

df_self_spent_prop_raw = df.groupby('identity')['self_spent_proportion'].mean()

df_mean_fee_per_transaction.corr(df_self_spent_prop_raw)


-0.049798379838131165

There is no clear linear relation between those two variables. In other terms, the fact that an actor issues a higher or lower proportion of auto transactions has no direct and predictable impact on the average fees it pays per transaction.

# Data merging

# Data merging

We will add data on the bitcoin price to evaluate the relation between the transactions and the price of bitcoin.

In [18]:
# load the external.csv file in timeseries folder
df_external = pd.read_csv('timeseries/external.csv', index_col=0, parse_dates=True)
df_external.head()

date    PriceUSD       HashRate
2190  2015-01-02  315.942732  333345.017260
2191  2015-01-03  285.647310  327284.198765
2192  2015-01-04  263.334575  347486.927083
2193  2015-01-05  275.003852  315162.561773
2194  2015-01-06  287.549521  319203.107437

In [19]:
df_external.dtypes


date         object
PriceUSD    float64
HashRate    float64
dtype: object

Let's convert the date column to datetime format and set it as the index of the DataFrame.

In [20]:
# convert the date in datetime format year-month-day
df_external['date'] = pd.to_datetime(df_external['date'], format='%Y-%m-%d')
df_external.head()

date    PriceUSD       HashRate
2190 2015-01-02  315.942732  333345.017260
2191 2015-01-03  285.647310  327284.198765
2192 2015-01-04  263.334575  347486.927083
2193 2015-01-05  275.003852  315162.561773
2194 2015-01-06  287.549521  319203.107437

Now let's add the column PriceUSD from the df_external to our principal Dataframe for corresponding date in both Dataframes.

In [21]:
df['PriceUSD'] = df['date'].map(df_external.set_index('date')['PriceUSD'])
df.tail()

year  month  day      identity  received  nb_received       date  \
90398  2017      6   17    BTCJam.com       0.0            0 2017-06-17   
90399  2017      6   18          7277       0.0            0 2017-06-18   
90400  2017      6   22      70063369       0.0            0 2017-06-22   
90401  2017      6   29  Loanbase.com       0.0            0 2017-06-29   
90402  2017      6   29          7277       0.0            0 2017-06-29   

          sum_fee  mean_fee_for100  nb_transactions        sent  self_spent  \
90398    145053.0         8.643929                1   1387984.0         0.0   
90399  26600900.0        49.327293              266    725280.0         0.0   
90400    284134.0         0.301961                1  93527891.0         0.0   
90401    131862.0         1.415791                1   9049938.0         0.0   
90402  39601350.0        49.327299              396   1079730.0         0.0   

       self_spent_estimated  nb_spent       spent  self_spent_proportion  \
90398                   0.0         2   1387984.0                    0.0   
90399                   0.0       532    725280.0                    0.0   
90400                   0.0         1  93527891.0                    0.0   
90401                   0.0         2   9049938.0                    0.0   
90402                   0.0       792   1079730.0                    0.0   

          PriceUSD  
90398  2652.755363  
90399  2508.214207  
90400  2686.647514  
90401  2540.443032  
90402  2540.443032

In [22]:

# sort the df by date
df = df.sort_values(by='date')

fig_price = px.line(df, x='date', y='PriceUSD', title='Evolution of the price of bitcoin (2015-2017)', labels={'value':'Price (USD)'})
fig_price.show()

In [23]:
# total number of transactions per day
df_nb_transactions = df.groupby('date')['nb_transactions'].sum()

# bitcoin price per day
df_price = df.groupby('date')['PriceUSD'].mean()

# we normalize the data in order to have the same scale for the 2 series : df_nb_transactions and df_price
df_nb_transactions_norm = (df_nb_transactions - df_nb_transactions.min()) / (df_nb_transactions.max() - df_nb_transactions.min())
df_price_norm = (df_price - df_price.min()) / (df_price.max() - df_price.min())


#  we plot the evolution of the number of transactions and the price of bitcoin per date
fig = go.Figure()
fig.add_trace(go.Scatter(x=df_nb_transactions_norm.index, y=df_nb_transactions_norm.values, name='Number of transactions'))
fig.add_trace(go.Scatter(x=df_price_norm.index, y=df_price_norm.values, name='Price of bitcoin'))
fig.update_layout(title='Evolution of the number of transactions and the price of bitcoin per date', xaxis_title='Date', yaxis_title='Normalized values')
fig.show()





 Concerning the relationship between Bitcoin's price and the number of transactions, the evidence suggests that there is no significant correlation between the two. While it is true that an increase in the number of transactions can result in higher fees, which could affect the demand for Bitcoin, other factors such as investor sentiment, market adoption, and macroeconomic conditions are likely to play a more significant role in determining Bitcoin's price.

 Nevertheless, we can observe that the number of transactions has increased significantly in 2015, let's try to understand why.



In [24]:
# plot df_nb_transactions between june and october 2015
fig_nb_transactions = px.line(df_nb_transactions['2015-06-01':'2015-10-31'], title='Number of transactions June-October 2015', labels={'value':'Number of transactions'})
fig_nb_transactions.show()

Blockchain marking events in 2015:

* **July, 2015**: Bitcoin Improvement Proposal 65 (BIP 65) was activated. This proposal introduced a new opcode called `OP_CHECKLOCKTIMEVERIFY` (CLTV), which allows transactions to be locked until a certain time or block height.

* **August 1, 2015**: Bitcoin Improvement Proposal 66 (BIP 66) was launched. BIP 66 proposed to replace the existing Secure Hash Algorithm (SHA-1) with the more secure `Secure Hash Algorithm (SHA-256)` for digital signatures used in Bitcoin transactions.

* **September 1, 2015**: `Bitcoin Core version 0.11.0` was released, with multiple features and improvements, such as faster block propagation, improved network security, and enhanced transaction broadcasting. 





The mentioned events can partially explain the significant increase in transactions during the corresponding periods as they brought improvements in the security of the blockchain. All of these improvements have contributed to a more secure and efficient Bitcoin blockchain, which has helped to increase user adoption and confidence in the technology. 

It is very interesting to analyse why the number of transactions increase because this can be seen as a positive development for the blockchain network and the Bitcoin, as it indicates that more people are using it for transactions and other purposes.
